In [371]:
import numpy as np

import pandas as pd
from IPython.display import display, HTML
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 50) #  columns count
pd.set_option('display.max_colwidth', -1)  # columns width 

# Use 3 decimal places in output display
pd.set_option("display.precision", 3)

# Don't wrap repr(DataFrame) across additional lines
pd.set_option("display.expand_frame_repr", False)


In [372]:
# file pathes to input data
fp_ut = 'UT.csv'     
fp_buh =  'BUH.csv'

In [373]:
# Describe field names
# F means Field
F_ITEM = 'Номенклатура'
F_CODE = 'КодНоменклатуры'
F_SUM = 'Сумма'
F_QUAN = 'Количество'
F_SERIESCODE = 'КодСерии'

In [374]:
# ABOUT THE DATA
# both files has similar columns but the UT has additional columns 'Серия', "КодСерии"
# both files has 'quantity' and 'sum' fields

float_type_rows = [F_QUAN, F_SUM] # the specifeid field will be converted to float

In [375]:
# clean up data for the given Series
def clean_up_for_numeric(given_df, df_name, col_name):
    '''col_name - column name for cleaning '''
    given_df[col_name].replace(u'\xa0',u'', regex=True, inplace=True) # clean up the no-break spaces
    given_df[col_name].replace(u',',u'.', regex=True, inplace=True)  # repalce commas with the dots
    print("Cleaning data in ",col_name," column successfull for", df_name)
    return True

# converts the given series to a float type
def convert_to_float(given_df, df_name, col_name): # 'df_name is the name of the datframe
    given_df[col_name] = given_df[col_name].astype(float)
    print("Converting ", col_name, " column in float successful for ", df_name)
    return True

In [376]:
df_ut = pd.read_csv(fp_ut, sep=';', dtype={F_SERIESCODE: 'str',F_CODE:'str'})
##df_ut = pd.read_excel(fp_ut, dtype={F_SERIESCODE: 'str',F_CODE:'str'})
df_buh = pd.read_csv(fp_buh,sep=';', dtype={F_CODE: 'str'}) 
##df_buh = pd.read_excel(fp_buh, dtype={F_CODE: 'str'}) 

In [377]:
df_ut['ЭтоБухгалтерия'] = False # to distinguish ut.csv rows from buh.csv
df_buh['ЭтоБухгалтерия'] = True # ADDING FLAG TO MARK THE RECORDS AS BUH

In [378]:
# Clean up the data in buh_ut
#    Convert Quantity and Sum fields to numeric
#    the quantity column may have a \xa0 symbol (no-break space)
# To figure out the value which can not be converted use: df.apply(pd.to_numeric)

# Remove NB spaces and replace commas with dots for columns Quantity and Sum
for float_col_name in float_type_rows:
        clean_up_for_numeric(df_buh, 'df_buh', float_col_name)
        convert_to_float(df_buh, 'df_buh', float_col_name)
        
        clean_up_for_numeric(df_ut, 'df_ut', float_col_name)
        convert_to_float(df_ut, 'df_ut', float_col_name)

Cleaning data in  Количество  column successfull for df_buh
Converting  Количество  column in float successful for  df_buh
Cleaning data in  Количество  column successfull for df_ut
Converting  Количество  column in float successful for  df_ut
Cleaning data in  Сумма  column successfull for df_buh
Converting  Сумма  column in float successful for  df_buh
Cleaning data in  Сумма  column successfull for df_ut
Converting  Сумма  column in float successful for  df_ut


In [379]:
print(df_buh.dtypes)
print(df_ut.dtypes)

Номенклатура       object 
КодНоменклатуры    object 
Склад              object 
Количество         float64
Сумма              float64
ЭтоБухгалтерия     bool   
dtype: object
Номенклатура       object 
КодНоменклатуры    object 
Склад              object 
Количество         float64
Сумма              float64
Серия              object 
КодСерии           object 
ЭтоБухгалтерия     bool   
dtype: object


In [380]:
DF_UT_rows = df_ut.shape[0]
print(df_ut.shape)
print(df_ut.sum(numeric_only=True)) # output SUMM
df_ut = df_ut.sort_values(by=[F_CODE])

(32877, 8)
Количество        1.041e+06
Сумма             0.000e+00
ЭтоБухгалтерия    0.000e+00
dtype: float64


In [381]:
DF_BUH_rows = df_buh.shape[0]
print(df_buh.shape) # 
print(df_buh.sum(numeric_only=True)) # output SUMM
df_buh = df_buh.sort_values(by=[F_CODE])

(29259, 6)
Количество        1.041e+06
Сумма             2.303e+09
ЭтоБухгалтерия    2.926e+04
dtype: float64


In [382]:
# CONCATENTATION OF buh and ut
df = pd.concat([df_ut, df_buh], sort=True)
df.reset_index(drop=True)

КодНоменклатуры   КодСерии  Количество                                                                                         Номенклатура                      Серия                         Склад      Сумма  ЭтоБухгалтерия
0      00000000012     000018136  138.00      Амортизатор (подушка) двигателя АКСС-400М                                                            2-032629112019N00197-24    Склад №2 Жабский В.           0.000e+00  False         
1      00000000012     000017723  1.00        Амортизатор (подушка) двигателя АКСС-400М                                                            2-032608112019N00133-21    Склад Костанай                0.000e+00  False         
2      00000000012     000015455  19.00       Амортизатор (подушка) двигателя АКСС-400М                                                            2-032618092019N00322-42    Склад Державинск              0.000e+00  False         
3      00000000012     000018136  60.00       Амортизатор (подушка) двигателя АКСС-400М                                                            2-032629112019N00197-24    Склад Костанай                0.000e+00  False         
4      00000000012     000018136  8.00        Амортизатор (подушка) двигателя АКСС-400М                                                            2-032629112019N00197-24    Cклад Петропавловск           0.000e+00  False         
5      00000000012     000017723  20.00       Амортизатор (подушка) двигателя АКСС-400М                                                            2-032608112019N00133-21    Склад Шкутько Д.П.            0.000e+00  False         
6      00000000012     000011869  10.00       Амортизатор (подушка) двигателя АКСС-400М                                                            2-032623072019N00178-1     Склад Шкутько Д.П.            0.000e+00  False         
7      00000000012     000011869  4.00        Амортизатор (подушка) двигателя АКСС-400М                                                            2-032623072019N00178-1     Cклад Петропавловск           0.000e+00  False         
8      00000000013     000011868  2.00        Амортизатор (подушка) КПП АКСС-220М                                                                  2-032615072019N00067-1     Склад Державинск              0.000e+00  False         
9      00000000013     000017722  4.00        Амортизатор (подушка) КПП АКСС-220М                                                                  2-032608112019N00133-20    Склад Нейвирт В.В.            0.000e+00  False         
10     00000000013     000015454  10.00       Амортизатор (подушка) КПП АКСС-220М                                                                  2-032618092019N00322-41    Склад Шкутько Д.П.            0.000e+00  False         
11     00000000013     000018135  12.00       Амортизатор (подушка) КПП АКСС-220М                                                                  2-032629112019N00197-23    Cклад Петропавловск           0.000e+00  False         
12     00000000013     000011868  24.00       Амортизатор (подушка) КПП АКСС-220М                                                                  2-032615072019N00067-1     Склад Шкутько Д.П.            0.000e+00  False         
13     00000000013     000017722  11.00       Амортизатор (подушка) КПП АКСС-220М                                                                  2-032608112019N00133-20    Склад №2 Жабский В.           0.000e+00  False         
14     00000000013     000018135  29.00       Амортизатор (подушка) КПП АКСС-220М                                                                  2-032629112019N00197-23    Склад №2 Жабский В.           0.000e+00  False         
15     00000000013     000018135  7.00        Амортизатор (подушка) КПП АКСС-220М                                                                  2-032629112019N00197-23    Склад Костанай                0.000e+00  False         
16     00000000013     000017722  20.00       Амортизатор (подушка) КПП АКСС-220М               

In [383]:
df[F_CODE] = df[F_CODE].astype(str) # convert to string
df[F_CODE] = df[F_CODE].str.strip() # removing whitespace
df[F_CODE] = df[F_CODE].replace('nan','')

In [384]:
df[F_QUAN] = df[F_QUAN].fillna(0.0)
df[F_QUAN] = df[F_QUAN].astype(float)

In [385]:
df.to_excel('UT_BUH.xlsx',index_label=False,index=False)

In [386]:
print("United DF, rows:", df.shape[0]," cols:",df.shape[1])

United DF, rows: 62136  cols: 8


In [387]:
subset_of_rows=[F_CODE,F_ITEM,'Склад']
#subset_of_rows=[F_CODE,'Склад'] # CHANGED
duplicated_df_series = df.duplicated(subset=subset_of_rows,keep=False)

In [388]:
# Select all duplicate rows based on all columns
duplicateRowsDF = df[duplicated_df_series]
duplicateRowsDF = duplicateRowsDF.reset_index(drop=True)

In [389]:
print("Duplicates DF, rows:",duplicateRowsDF.shape[0]," cols:",duplicateRowsDF.shape[1])

Duplicates DF, rows: 62113  cols: 8


In [390]:
df.sum(numeric_only=True)

Количество        2.081e+06
Сумма             2.303e+09
ЭтоБухгалтерия    2.926e+04
dtype: float64

In [391]:
DF_rows_before_reducing = df.shape[0]
print("DF before duplicates removing, rows:",df.shape[0]," cols:",df.shape[1])
DF_SUM_BEFORE = df.sum(numeric_only=True)
print(DF_SUM_BEFORE["Сумма"])

DF before duplicates removing, rows: 62136  cols: 8
2303474637.120004


In [392]:
# Removing intersection of 2 UT and BUH by their intersection
df.drop_duplicates(subset=subset_of_rows, 
                     keep = False, inplace = True) 
print(df.shape)
DF_rows_AFTER_reducing = df.shape[0]
DF_SUM_AFTER = df.sum(numeric_only=True)

(23, 8)


In [393]:
##df

In [394]:
duplicateRowsDF_rows_number = duplicateRowsDF.shape[0]
duplicateRowsDF_summ = duplicateRowsDF.sum(numeric_only=True)

In [395]:
print("DF_UT_rows:",DF_UT_rows)
print("DF_BUH_row:",DF_BUH_rows)
print()
print("DF_rows_before_reducing:",DF_rows_before_reducing)
print("DF_rows_AFTER_reducing:",DF_rows_AFTER_reducing)
print()
print("duplicateRowsDF_rows_number:",duplicateRowsDF_rows_number)

DF_UT_rows: 32877
DF_BUH_row: 29259

DF_rows_before_reducing: 62136
DF_rows_AFTER_reducing: 23

duplicateRowsDF_rows_number: 62113


In [396]:
print("*******************")
print("Сумма до удаления дублей:",DF_SUM_BEFORE["Сумма"]) 
print("Сумма после удаления дублей:",DF_SUM_AFTER["Сумма"])
print()
print("Сумма дубликатов:            ", duplicateRowsDF_summ["Сумма"])
print('разница до от разницы после', round(DF_SUM_BEFORE["Сумма"]-DF_SUM_AFTER["Сумма"], 2)) # если тут разнциа то это ошибка

*******************
Сумма до удаления дублей: 2303474637.120004
Сумма после удаления дублей: 352502.68

Сумма дубликатов:             2303122134.440004
разница до от разницы после 2303122134.44


In [397]:
print("rows dupl",duplicateRowsDF.shape[0])
print(duplicateRowsDF.sum(numeric_only=True))

rows dupl 62113
Количество        2.081e+06
Сумма             2.303e+09
ЭтоБухгалтерия    2.924e+04
dtype: float64


In [398]:
# As far as the the buh.csv has no "СерияНоменклатуры" field consider the rows of subset from buh as unique
rows_of_buh = duplicateRowsDF[duplicateRowsDF['ЭтоБухгалтерия'] == True]

In [399]:
print(rows_of_buh.shape)
print(rows_of_buh.sum(numeric_only=True))

(29240, 8)
Количество        1.041e+06
Сумма             2.303e+09
ЭтоБухгалтерия    2.924e+04
dtype: float64


In [400]:
counter = 0
size_of_rows = rows_of_buh.shape[0]
for index, row in rows_of_buh.iterrows():   
    ##print("TEMP SERIES BEGIN")
    ##print("***************************************")
    #query_string = 'КодНоменклатуры == \''+row[F_CODE]+'\' and Номенклатура ==\"'+row[F_ITEM]+'\" and Склад == \''+row['Склад']+'\''
    #query_string = 'Номенклатура ==\''+row[F_ITEM]+'\''
#     temp_df  = duplicateRowsDF.query(query_string, inplace = False)
#     print("<<",row[F_ITEM],">>","length:",len(row[F_ITEM]))
#     print("<<",rows_of_buh[F_ITEM].iloc[0],">>","length:",len(rows_of_buh[F_ITEM].iloc[0]))
#     print(row[F_ITEM] == rows_of_buh[F_ITEM].iloc[0])
#     print("@@@")
#     print(query_string) 
#     print("@@")
    temp_df  = duplicateRowsDF.query('КодНоменклатуры == \''+row[F_CODE]+'\' and Склад == \''+row['Склад']+'\'', inplace = False)
    buh_sum = row[F_SUM]
    counter+=1
    print("counter:",counter,"/",size_of_rows)
    ##print("бухгалтерская сумма:", buh_sum)  
        
    # Removing the buh string from temp_df otherwirse I won't be able to count the quantity of series in UT
    ##############################
    # Get names of indices for which ЭтоБухгалтерия is true
    indexNames = temp_df[temp_df['ЭтоБухгалтерия'] == True ].index
    # Delete these row indices from dataFrame
    temp_df.drop(indexNames , inplace=True)
    ##############################
    
    temp_number_of_series = temp_df[F_QUAN].sum() 
    ##print("Количество по сериям: ",temp_number_of_series) 
    
    # define the price
    if temp_number_of_series != 0:
        price = buh_sum / temp_number_of_series
        price = round(price,2)
    else:
        price = 0.0
        
    ##print("Price of series is:", price)
    
    summ_accum = 0.0 # the_sum_remains check 
    
    # Summ distribution to series 
    for temp_index,temp_row in temp_df.iterrows():
        current_sum = price * temp_row[F_QUAN]
        duplicateRowsDF.at[temp_index,F_SUM] = round(current_sum,2)
        ##print("Teh summ is", duplicateRowsDF.at[temp_index,F_SUM])
        the_last_index = temp_index  # hope it won't clear iself after the loop
        summ_accum+=round(current_sum,2)
        
    # the_sum_remains check
    if summ_accum != buh_sum:
        print("difference in ",row[F_CODE],row[F_ITEM],row['Склад'], " sum if difference between ",buh_sum," and ",summ_accum)
        summ_dif = buh_sum - summ_accum
        duplicateRowsDF.at[the_last_index, F_SUM] += round(summ_dif,2)  # add the sum to the last row with the series
  
    ##display(temp_df)

counter: 1 / 29240
difference in  00000000012 Амортизатор (подушка) двигателя АКСС-400М Склад Державинск  sum if difference between  50750.49  and  50750.52
counter: 2 / 29240
difference in  00000000012 Амортизатор (подушка) двигателя АКСС-400М Склад №2 Жабский В.  sum if difference between  393545.81  and  393545.64
counter: 3 / 29240
difference in  00000000012 Амортизатор (подушка) двигателя АКСС-400М Cклад Петропавловск  sum if difference between  33494.01  and  33494.04
counter: 4 / 29240
counter: 5 / 29240
difference in  00000000012 Амортизатор (подушка) двигателя АКСС-400М Склад Костанай  sum if difference between  173908.28  and  173908.56
counter: 6 / 29240
counter: 7 / 29240
difference in  00000000013 Амортизатор (подушка) КПП АКСС-220М  Cклад Петропавловск  sum if difference between  25536.15  and  25536.12
counter: 8 / 29240
difference in  00000000013 Амортизатор (подушка) КПП АКСС-220М  Склад №2 Жабский В.  sum if difference between  85124.65  and  85124.8
counter: 9 / 2924

counter: 79 / 29240
difference in  00000000032 Вал привода угл. редуктора КПП К-700/701 700А.17.01.191 Склад Костанай  sum if difference between  35646.29  and  35646.28
counter: 80 / 29240
counter: 81 / 29240
difference in  00000000032 Вал привода угл. редуктора КПП К-700/701 700А.17.01.191 Склад №2 Жабский В.  sum if difference between  39917.43  and  39917.44
counter: 82 / 29240
counter: 83 / 29240
counter: 84 / 29240
difference in  00000000033 Вал ведущий КПП К-700/701 в сборе Склад №2 Жабский В.  sum if difference between  3052714.28  and  3052714.26
counter: 85 / 29240
difference in  00000000035 Вал гибкий в сборе (трос тахоспидометра) К-700/701 700А.00.17.160 Склад Шкутько Д.П.  sum if difference between  5141.22  and  5141.2
counter: 86 / 29240
counter: 87 / 29240
counter: 88 / 29240
counter: 89 / 29240
difference in  00000000037 Вал карданный КПП К-700А 700.22.08.000-2  Склад №2 Жабский В.  sum if difference between  67884.73  and  67884.72
counter: 90 / 29240
counter: 91 / 29

counter: 170 / 29240
difference in  00000000057 Гайка М12х1,25 малого болта кардана К-700/701  Склад Шкутько Д.П.  sum if difference between  669.3  and  669.5
counter: 171 / 29240
difference in  00000000057 Гайка М12х1,25 малого болта кардана К-700/701  Склад бр Оберемко В.  sum if difference between  1307.88  and  1308.0
counter: 172 / 29240
difference in  00000000057 Гайка М12х1,25 малого болта кардана К-700/701  Склад Костанай  sum if difference between  2007.9  and  2008.5
counter: 173 / 29240
difference in  00000000058 Гайка колеса К-700/701 М20х1,5 Склад №2 Жабский В.  sum if difference between  4064.51  and  4064.56
counter: 174 / 29240
counter: 175 / 29240
difference in  00000000058 Гайка колеса К-700/701 М20х1,5 Склад бр Оберемко В.  sum if difference between  5077.47  and  5077.44
counter: 176 / 29240
counter: 177 / 29240
difference in  00000000058 Гайка колеса К-700/701 М20х1,5 Склад Костанай  sum if difference between  9719.47  and  9719.6
counter: 178 / 29240
difference i

counter: 258 / 29240
difference in  00000000085 Головка компрессора ЗИЛ/К-700 (К) Cклад Петропавловск  sum if difference between  10767.85  and  10767.84
counter: 259 / 29240
counter: 260 / 29240
counter: 261 / 29240
counter: 262 / 29240
difference in  00000000087 Распределитель с редуктором (ГУР) К-700/701 Склад Костанай  sum if difference between  198747.52  and  198747.51
counter: 263 / 29240
counter: 264 / 29240
difference in  00000000087 Распределитель с редуктором (ГУР) К-700/701 Склад №2 Жабский В.  sum if difference between  177201.08  and  177201.09
counter: 265 / 29240
difference in  00000000088 Датчик давления масла двигателя (10 атм) К-700/701 г.Владимир Склад №2 Жабский В.  sum if difference between  316914.67  and  316915.2
counter: 266 / 29240
difference in  00000000088 Датчик давления масла двигателя (10 атм) К-700/701 г.Владимир Склад Шкутько Д.П.  sum if difference between  11876.29  and  11876.3
counter: 267 / 29240
counter: 268 / 29240
difference in  00000000088 Дат

counter: 340 / 29240
difference in  00000000106 Клапан впускной ЯМЗ,ДТ,Т-4 /продавать в паре с выпускным/ (ОАО Автодизель-ЯМЗ)   Склад Державинск  sum if difference between  11979.92  and  11979.9
counter: 341 / 29240
counter: 342 / 29240
counter: 343 / 29240
difference in  00000000106 Клапан впускной ЯМЗ,ДТ,Т-4 /продавать в паре с выпускным/ (ОАО Автодизель-ЯМЗ)   Склад №4 Бавин И.  sum if difference between  183797.27  and  183796.86
counter: 344 / 29240
difference in  00000000106 Клапан впускной ЯМЗ,ДТ,Т-4 /продавать в паре с выпускным/ (ОАО Автодизель-ЯМЗ)   Cклад Петропавловск  sum if difference between  39037.99  and  39038.04
counter: 345 / 29240
difference in  00000000107 Клапан выпускной ЯМЗ,ДТ,Т-4 (ОАО Автодизель-ЯМЗ)   Склад Костанай  sum if difference between  186720.33  and  186720.44
counter: 346 / 29240
counter: 347 / 29240
difference in  00000000107 Клапан выпускной ЯМЗ,ДТ,Т-4 (ОАО Автодизель-ЯМЗ)   Склад №4 Бавин И.  sum if difference between  661432.46  and  661432.25

...

counter: 28648 / 29240
difference in  014779 4000 Д(Г) Ремень приводной (Ярославль) Максимов В.И.  sum if difference between  26785.71  and  26785.8
counter: 28649 / 29240
difference in  014780 Указатель поворота боковой МАЗ (РБ) Склад №2 Жабский В.  sum if difference between  5644.57  and  5644.6
counter: 28650 / 29240
counter: 28651 / 29240
counter: 28652 / 29240
counter: 28653 / 29240
difference in  014787 Транспортер наклонной камеры Вектор /1070мм/ планка 3мм на заклепках /Россия/ Склад №3 Нейвирт В./Серба В.  sum if difference between  250312.58  and  250312.59
counter: 28654 / 29240
counter: 28655 / 29240
difference in  014788 Транспортер наклонной камеры Вектор /1070мм/ нов. обр. 52 планки 4мм УСИЛЕННЫЙ., на болтах /Россия/ Склад №3 Нейвирт В./Серба В.  sum if difference between  382606.44  and  382606.4
counter: 28656 / 29240
difference in  014790 Форсунка Д-245/260Е2 /аналог 172.1112010-11.01/ под распылитель 335-120 (ОАО ЯЗДА) Склад № 1  sum if difference between  86961.17  

counter: 28843 / 29240
counter: 28844 / 29240
counter: 28845 / 29240
counter: 28846 / 29240
counter: 28847 / 29240
counter: 28848 / 29240
counter: 28849 / 29240
difference in  014976 Муфта упругая привода вентилятора ЯМЗ-236/238 (ЯЗТО) Склад № 1  sum if difference between  170419.8  and  170419.68
counter: 28850 / 29240
difference in  014976 Муфта упругая привода вентилятора ЯМЗ-236/238 (ЯЗТО) Cклад Петропавловск  sum if difference between  12623.69  and  12623.68
counter: 28851 / 29240
counter: 28852 / 29240
difference in  014976 Муфта упругая привода вентилятора ЯМЗ-236/238 (ЯЗТО) Склад Шкутько Д.П.  sum if difference between  28403.29  and  28403.28
counter: 28853 / 29240
counter: 28854 / 29240
counter: 28855 / 29240
difference in  014979 Звёздочка считывания оборотов (z=6, d=25мм) (Ростсельмаш) Склад №3 Нейвирт В./Серба В.  sum if difference between  36462.09  and  36462.1
counter: 28856 / 29240
counter: 28857 / 29240
counter: 28858 / 29240
counter: 28859 / 29240
difference in  014

counter: 28990 / 29240
counter: 28991 / 29240
difference in  015134 5300 Д(Г) Ремень приводной (РСМ 6201354) (Ярославль Премиум) Склад №4 Бавин И.  sum if difference between  100868.88  and  100868.8
counter: 28992 / 29240
difference in  015135 2000 С(В) Ремень приводной (РСМ 6201343) (Ярославль Премиум) Склад №4 Бавин И.  sum if difference between  91351.61  and  91351.44
counter: 28993 / 29240
difference in  015136 2120 С(В) Ремень приводной Енисей (Ярославль Премиум) Склад №4 Бавин И.  sum if difference between  115653.71  and  115653.66
counter: 28994 / 29240
difference in  015137 2240 С(В) Ремень приводной (Ярославль Премиум) Склад №4 Бавин И.  sum if difference between  25574.19  and  25574.22
counter: 28995 / 29240
difference in  015138 2650 С(В) ремень приводной (Ярославль Премиум) Склад №4 Бавин И.  sum if difference between  63872.78  and  63872.68
counter: 28996 / 29240
difference in  015139 3550 С(В) Ремень приводной (Ярославль Премиум) Склад №4 Бавин И.  sum if difference 

difference in  015201 Замок капота МТЗ-80/82 (р.Беларусь) Склад № 1  sum if difference between  4534.01  and  4534.02
counter: 29066 / 29240
counter: 29067 / 29240
counter: 29068 / 29240
counter: 29069 / 29240
counter: 29070 / 29240
counter: 29071 / 29240
counter: 29072 / 29240
counter: 29073 / 29240
counter: 29074 / 29240
counter: 29075 / 29240
counter: 29076 / 29240
counter: 29077 / 29240
counter: 29078 / 29240
counter: 29079 / 29240
counter: 29080 / 29240
counter: 29081 / 29240
difference in  015216 Втулка подшипника 212 под 1 стопор (СТС/СЗС/СКП) литая Склад №3 Нейвирт В./Серба В.  sum if difference between  214285.71  and  214286.0
counter: 29082 / 29240
difference in  015216 Втулка подшипника 212 под 1 стопор (СТС/СЗС/СКП) литая Cклад Петропавловск  sum if difference between  53571.43  and  53571.5
counter: 29083 / 29240
counter: 29084 / 29240
counter: 29085 / 29240
counter: 29086 / 29240
counter: 29087 / 29240
difference in  015227 Долото накладное левое (Рубцовск) Склад №2 Жабс

counter: 29205 / 29240
difference in  015438 Пружина отжимного рычага корзины Т-40 Максимов В.И.  sum if difference between  6321.43  and  6320.67
counter: 29206 / 29240
difference in  015441 Крестовина кардана Т-40 Максимов В.И.  sum if difference between  4285.71  and  4285.72
counter: 29207 / 29240
counter: 29208 / 29240
counter: 29209 / 29240
counter: 29210 / 29240
difference in  015445 Фильтр маслянный ЗИЛ-5301 БЫЧОК  Максимов В.И.  sum if difference between  8303.57  and  8303.97
counter: 29211 / 29240
counter: 29212 / 29240
counter: 29213 / 29240
counter: 29214 / 29240
difference in  015449 Вкладыши  шатунные П-23 (Р1)  Максимов В.И.  sum if difference between  1785.71  and  1785.72
counter: 29215 / 29240
difference in  015450 Редуктора бортового МТЗ-80/82 (РЕМ. К-Т.) Максимов В.И.  sum if difference between  27232.14  and  27232.23
counter: 29216 / 29240
difference in  015451 Прокладок коллектора КАМАЗ (РЕМ. К-Т.)(РУСЬ) Максимов В.И.  sum if difference between  4642.86  and  46

In [401]:
# save transition to file
###############################################################################################
duplicateRowsDF.to_excel('transition_duplicateRowsDF.xlsx',index_label=False,index=False,float_format='%.2f')

In [402]:
# Removing buh-string from duplicates dataframe - we've already got the sum to distibute among set of Series rows
###############################################################################################
# Get names of indexes for which ЭтоБухгалтерия is true
indexNames = duplicateRowsDF[duplicateRowsDF['ЭтоБухгалтерия'] == True ].index
# Delete these row indexes from dataFrame
duplicateRowsDF.drop(indexNames , inplace=True)
##############################

In [403]:
# adding fixed duplicates to the df
df = pd.concat([df, duplicateRowsDF], sort=True) # sets union
df.reset_index(drop=True)


КодНоменклатуры   КодСерии  Количество                                                                                         Номенклатура                               Серия                         Склад      Сумма  ЭтоБухгалтерия
0      009706          000006376  2.00        Прокладка колпака МТЗ (ОАО ММЗ) г.Минск                                                              1-032615032019N00624-18             Склад № 1                     0.000e+00  False         
1      009706          000005110  5.00        Прокладка колпака МТЗ (ОАО ММЗ) г.Минск                                                              1-032606092018N00156-60             Склад Державинск              0.000e+00  False         
2      012371          000012563  1.00        Бак топливный К-700А/701 /новый, желтый Ст/ левый                                                    2-032630072019N00614-2              Склад №2 Жабский В.           0.000e+00  False         
3      012372          000012562  1.00        Бак топливный К-700А/701 /новый, желтый Ст/ правый                                                   2-032630072019N00614-1              Склад №2 Жабский В.           0.000e+00  False         
4      00000000133     NaN        0.00        Крышка промежуточной опоры К-700/701                                                                 NaN                                 Склад №3 Нейвирт В./Серба В.  3.203e+02  True          
5      00000000574     NaN        0.00        РВД  ключ 24  L=1,0 м. (AGROIMPULS)                                                                  NaN                                 Склад №3 Нейвирт В./Серба В. -1.000e-02  True          
6      00000000575     NaN        0.00        РВД  ключ 24  L=1,2 м. (AGROIMPULS)                                                                  NaN                                 Склад №3 Нейвирт В./Серба В.  1.450e+00  True          
7      00000007265     NaN        0.00        Передача главная с дифференциалом 700А.23.02.000 (М)                                                 NaN                                 Склад №2 Жабский В.          -2.183e+03  True          
8      00000007536     NaN        0.00        РВД  ключ 24  L=1,4 м. (AGROIMPULS)                                                                  NaN                                 Склад №3 Нейвирт В./Серба В. -3.150e+00  True          
9      000758          NaN        0.00        Вод. насоса МТЗ стар. обр. (РЕМ. К-Т.)                                                               NaN                                 Склад № 1                     1.518e+02  True          
10     001638          NaN        0.00        Секция высокого давления 3- выхода (УРТ)                                                             NaN                                 Склад магазин Мергунов       -7.780e+00  True          
11     003600          NaN        0.00        КПП МТЗ-1221 (РЕМ. К-Т.)                                                                             NaN                                 Склад № 1                     3.037e+01  True          
12     004364          NaN        0.00        Муфта разрывная кл. 32 ДТ (AGROIMPULS) нов. обр. 1-но стор.                                          NaN                                 Склад №3 Нейвирт В./Серба В. -2.863e+01  True          
13     006224          NaN        0.00        Фланец кардана переднего Т-150/ХТЗ                                                                   NaN                                 Склад №3 Нейвирт В./Серба В.  4.124e+01  True          
14     006862          NaN        0.00        Гидрораспределитель Р80 МТЗ с гидрозамком (Гидролига)                                                NaN                                 Максимов В.И.                 1.843e+04  True          
15     007293          NaN        0.00        Стойка сеялки СЗС-2,1 стар. обр. большая верхняя прямая                                              NaN                                

In [404]:
df.shape

(32896, 8)

In [405]:
df.sum(numeric_only=True)["Количество"]

1040678.2399999996

In [406]:
round(df.sum(numeric_only=True)["Сумма"],2)

2303474637.12

In [407]:
df = df.sort_values(by=[F_CODE])

In [408]:
df

КодНоменклатуры   КодСерии  Количество                                                                                         Номенклатура                               Серия                         Склад      Сумма  ЭтоБухгалтерия
5      00000000012     000017723  20.00       Амортизатор (подушка) двигателя АКСС-400М                                                            2-032608112019N00133-21             Склад Шкутько Д.П.            5.585e+04  False         
2      00000000012     000015455  19.00       Амортизатор (подушка) двигателя АКСС-400М                                                            2-032618092019N00322-42             Склад Державинск              5.075e+04  False         
3      00000000012     000018136  60.00       Амортизатор (подушка) двигателя АКСС-400М                                                            2-032629112019N00197-24             Склад Костанай                1.711e+05  False         
4      00000000012     000018136  8.00        Амортизатор (подушка) двигателя АКСС-400М                                                            2-032629112019N00197-24             Cклад Петропавловск           2.233e+04  False         
6      00000000012     000011869  10.00       Амортизатор (подушка) двигателя АКСС-400М                                                            2-032623072019N00178-1              Склад Шкутько Д.П.            2.793e+04  False         
7      00000000012     000011869  4.00        Амортизатор (подушка) двигателя АКСС-400М                                                            2-032623072019N00178-1              Cклад Петропавловск           1.116e+04  False         
1      00000000012     000017723  1.00        Амортизатор (подушка) двигателя АКСС-400М                                                            2-032608112019N00133-21             Склад Костанай                2.851e+03  False         
0      00000000012     000018136  138.00      Амортизатор (подушка) двигателя АКСС-400М                                                            2-032629112019N00197-24             Склад №2 Жабский В.           3.935e+05  False         
14     00000000013     000018135  29.00       Амортизатор (подушка) КПП АКСС-220М                                                                  2-032629112019N00197-23             Склад №2 Жабский В.           6.172e+04  False         
13     00000000013     000017722  11.00       Амортизатор (подушка) КПП АКСС-220М                                                                  2-032608112019N00133-20             Склад №2 Жабский В.           2.341e+04  False         
16     00000000013     000017722  20.00       Амортизатор (подушка) КПП АКСС-220М                                                                  2-032608112019N00133-20             Склад Шкутько Д.П.            4.253e+04  False         
11     00000000013     000018135  12.00       Амортизатор (подушка) КПП АКСС-220М                                                                  2-032629112019N00197-23             Cклад Петропавловск           2.554e+04  False         
10     00000000013     000015454  10.00       Амортизатор (подушка) КПП АКСС-220М                                                                  2-032618092019N00322-41             Склад Шкутько Д.П.            2.127e+04  False         
9      00000000013     000017722  4.00        Амортизатор (подушка) КПП АКСС-220М                                                                  2-032608112019N00133-20             Склад Нейвирт В.В.            8.514e+03  False         
8      00000000013     000011868  2.00        Амортизатор (подушка) КПП АКСС-220М                                                                  2-032615072019N00067-1              Склад Державинск              4.306e+03  False         
15     00000000013     000018135  7.00        Амортизатор (подушка) КПП АКСС-220М                                                                  2-032629112019N00197-23            

In [409]:
# THE FINAL RESULT BEING MADE HERE
###############################################################################################
df.to_excel('final_UT_BUH.xlsx',index_label=False,index=False,float_format='%.2f')

In [413]:
df['Сумма'].sum()

2303474637.12

In [415]:
df['Количество'].sum()

1040678.24

In [163]:
# All code needed to check the difference of concatenating ut and buh listed below
###############################################################################################
# reread the new file
fp_changed ="final_UT_BUH.xlsx"
#df_changed = pd.read_csv(fp_changed, sep=';', encoding='cp1251', dtype={F_SERIESCODE: 'str',F_CODE:'str',F_QUAN:float})
df_changed = pd.read_excel(fp_changed)

In [236]:
df_changed.dtypes

КодНоменклатуры      int64
КодСерии           float64
Количество           int64
Номенклатура        object
Серия               object
Склад               object
Сумма              float64
ЭтоБухгалтерия        bool
dtype: object

In [237]:
print(df_changed.shape[0])
print()
print(df_ut.shape[0])

122

27


In [238]:
df_changed = df_changed.drop(['ЭтоБухгалтерия'],  axis = 1)

In [239]:
df_ut = df_ut.drop(['ЭтоБухгалтерия'],  axis = 1)

In [240]:
df_changed = df_changed.drop([F_SUM],  axis = 1)
df_ut = df_ut.drop([F_SUM],  axis = 1)

In [241]:
# ATTENTION!
# Code below check the data in memory from df variable! Not from xls file
############################################################################################

df_mem = df.copy(deep=True)  # deep=False - means no indices
# dropping unwanted columns
df_mem = df_mem.drop(['ЭтоБухгалтерия'],  axis = 1)
df_mem = df_mem.drop([F_SUM],  axis = 1)
# converting columns
df_mem[F_CODE] = df_mem[F_CODE].str.strip()
df_mem[F_SERIESCODE] = df_mem[F_SERIESCODE].str.strip()
df_mem[F_ITEM] = df_mem[F_ITEM].str.strip()
df_mem['Серия'] = df_mem['Серия'].str.strip()
df_mem['Склад'] = df_mem['Склад'].str.strip()
# show example
display(df_mem.head())
print(df_mem.dtypes)
df_mem.reset_index(inplace=True,drop=True)
#display(df_mem.head)
print(df_mem.columns.tolist())
print(df_mem.dtypes)
print(df_mem.shape)

КодНоменклатуры КодСерии  Количество  \
0       00000000678      NaN        42.0   
1       00000000804      NaN         3.0   
2       00000000814      NaN        50.0   
105     00000001227      NaN        20.0   
3       00000001285      NaN        17.0   

                                       Номенклатура Серия     Склад  
0                             Тяга регулятора ПД-10   NaN  Склад №1  
1               Манометр (0-10атм) мех-й. (14.3830)   NaN  Склад №1  
2    Реле-регулятор напряжения мех-й 12в (774.3702)   NaN  Склад №1  
105              Манометр (0-6 атм) мех-й.(11.3816)   NaN  Склад №1  
3                         Манометр (0-16атм) мех-й.   NaN  Склад №1

КодНоменклатуры     object
КодСерии            object
Количество         float64
Номенклатура        object
Серия               object
Склад               object
dtype: object
['КодНоменклатуры', 'КодСерии', 'Количество', 'Номенклатура', 'Серия', 'Склад']
КодНоменклатуры     object
КодСерии            object
Количество         float64
Номенклатура        object
Серия               object
Склад               object
dtype: object
(122, 6)


In [242]:
df_mem.head()

КодНоменклатуры КодСерии  Количество  \
0     00000000678      NaN        42.0   
1     00000000804      NaN         3.0   
2     00000000814      NaN        50.0   
3     00000001227      NaN        20.0   
4     00000001285      NaN        17.0   

                                     Номенклатура Серия     Склад  
0                           Тяга регулятора ПД-10   NaN  Склад №1  
1             Манометр (0-10атм) мех-й. (14.3830)   NaN  Склад №1  
2  Реле-регулятор напряжения мех-й 12в (774.3702)   NaN  Склад №1  
3              Манометр (0-6 атм) мех-й.(11.3816)   NaN  Склад №1  
4                       Манометр (0-16атм) мех-й.   NaN  Склад №1

In [243]:
df_ut[F_CODE] = df_ut[F_CODE].str.strip()
df_ut[F_SERIESCODE] = df_ut[F_SERIESCODE].str.strip()
df_ut[F_ITEM] = df_ut[F_ITEM].str.strip()
df_ut['Серия'] = df_ut['Серия'].str.strip()
df_ut['Склад'] = df_ut['Склад'].str.strip()

print(df_ut.columns.tolist())

print(df_ut.dtypes)

df_ut = df_ut.reindex(columns=df_mem.columns.tolist())
print(df_ut.reset_index(inplace=True,drop=True))
print(df_ut.shape)

['Номенклатура', 'КодНоменклатуры', 'Склад', 'Количество', 'Серия', 'КодСерии']
Номенклатура        object
КодНоменклатуры     object
Склад               object
Количество         float64
Серия               object
КодСерии            object
dtype: object
None
(27, 6)


In [244]:
df_ut.head()

КодНоменклатуры КодСерии  Количество  \
0     00000000678      NaN        42.0   
1     00000000804      NaN         3.0   
2     00000000814      NaN        50.0   
3     00000001285      NaN        17.0   
4     00000001950      NaN        50.0   

                                     Номенклатура Серия     Склад  
0                           Тяга регулятора ПД-10   NaN  Склад №1  
1             Манометр (0-10атм) мех-й. (14.3830)   NaN  Склад №1  
2  Реле-регулятор напряжения мех-й 12в (774.3702)   NaN  Склад №1  
3                       Манометр (0-16атм) мех-й.   NaN  Склад №1  
4                       Термостат МТЗ (ТС-117-04)   NaN  Склад №1

In [245]:
# Check columns names for equality
################################
cols1 = df_mem.columns.tolist()
cols2 = df_ut.columns.tolist()
print(cols1)
print(cols2)
if cols1 == cols2:
    print('column names are equal')

['КодНоменклатуры', 'КодСерии', 'Количество', 'Номенклатура', 'Серия', 'Склад']
['КодНоменклатуры', 'КодСерии', 'Количество', 'Номенклатура', 'Серия', 'Склад']
column names are equal


In [246]:
# Code below used for column content collisions
#############################################################
# eg I found the rows with same code but different names - 
# it means the same item in UT and Buh has the different names but the same code

# specify the column to search for duplicates
#COL_NAME = F_CODE
COL_NAME = F_ITEM

# Prepare the first set 
df_mem_items = list(set(df_mem[COL_NAME].tolist())) # Column folding - get All unique codes of items
print(len(df_mem_items))
df_mem_items.sort()
print(df_mem_items[:10]) # show 10 

# Prepare the second set 
ut_mem_items = list(set(df_ut[COL_NAME].tolist())) # column folding
print(len(ut_mem_items))
ut_mem_items.sort()
print(ut_mem_items[:10])

 
# Function to get the intersection of two lists using set() method 
def intersection(lst1, lst2): 
    return list(set(lst1) & set(lst2)) 

common_values = intersection(df_mem_items, ut_mem_items) # get the intersection

print(len(common_values)) # how many common items in common items set
print(common_values[:10])

print("len of df_mem_items ", len(df_mem_items)) # how many common items in the first set
print()

# MAKING LIST OF UNIQUE CODES FROM df_mem
##############################################
df_mem_count_of_unique_values = 0
df_mem_unique_values = []
# unique df_mem_items
for code in df_mem_items:
    if code not in common_values:
        df_mem_unique_values.append(code)
        df_mem_count_of_unique_values += 1    
print("Number of unique values in df_mem_items", df_mem_count_of_unique_values)
print()
print(df_mem_unique_values)

# MAKING LIST OF UNIQUE CODES FROM df_mem
##############################################
df_ut_count_of_unique_values = 0
df_ut_unique_values = []
# unique df_mem_items
for code in ut_mem_items:
    if code not in common_values:
        df_ut_unique_values.append(code)
        df_ut_count_of_unique_values += 1
        
print("Number of unique values in df_ut ", df_ut_count_of_unique_values)
print()
print(df_ut_unique_values)

120
['Амортизатор рулевого вала МТЗ-80/82', 'Башмак плуга отвального ПЛЕ ЛИТОЙ (Рубцовск)', 'Болт карданный МТЗ-82 М10х1 с гайкой', 'Болт ступицы переднего колеса МТЗ/ЮМЗ', 'Болт шкива коленвала МТЗ', 'Вал гибкий в сборе (трос тахоспидометра) МТЗ, ГАЗ-53 1570мм', 'Вал карданный переднего моста МТЗ-1221', 'Вал привода рулевого управления МТЗ  80-3401072', 'Валик МТЗ  70-1601140', 'Вилка переключения управления понижающим редуктором МТЗ  80-1723021']
25
['Датчик давления масла МТЗ нов. обр.(2 тонких шт.)', 'Датчик температуры двигателя МТЗ нов. обр.', 'Зеркало заднего вида МТЗ боковое 80-8201050', 'Кольцо гильзы фторопластовое МТЗ', 'Корпус дифф-ла заднего моста МТЗ-80/82', 'Кран ВС-11', 'Кран топливный ПП6-1/КР-25/МТЗ', 'Кронштейн крепления гидроцилиндра ГОРУ МТЗ Ф80-3001011', 'Манометр (0-10атм) мех-й. (14.3830)', 'Манометр (0-16атм) мех-й.']
25
['Переключатель освещения клавишный МТЗ', 'Реле-регулятор напряжения мех-й 12в (774.3702)', 'Термостат МТЗ (ТС-117-04)', 'Щетка стеклоочистите

In [247]:
df_names_are_different_in_UT_BUH = df_mem[df_mem[COL_NAME].isin(df_mem_unique_values)]

In [248]:
df_ut[df_ut[F_CODE].isin(df_mem_unique_values)] # empty is right

Empty DataFrame
Columns: [КодНоменклатуры, КодСерии, Количество, Номенклатура, Серия, Склад]
Index: []

In [249]:
print(df_mem.shape)
print(df_ut.shape)
common = df_mem.merge(df_ut,on=[F_CODE,F_SERIESCODE,F_ITEM,'Серия','Склад',F_QUAN])
print(common.shape) #

(122, 6)
(27, 6)
(27, 6)


In [250]:
# out the dif in excel
df_names_are_different_in_UT_BUH.to_excel('different_names.xlsx',index_label=False,index=False,float_format='%.2f') 